In [4]:
import pandas as pd
import numpy as np
import torch
import torch.nn as nn
from torch.utils.data import TensorDataset, DataLoader
from torch import Tensor
import torch.nn.functional as F
from torch.optim.lr_scheduler import MultiStepLR
from torch.utils.tensorboard import SummaryWriter

In [5]:
# Convolutional neural network (two convolutional layers)
class BiGRU(nn.Module):
    def __init__(self, num_classes=4):
        super(BiGRU, self).__init__()
           
        self.d1 = nn.Dropout(p=0.25)      
        self.bn1 = nn.BatchNorm1d(64,affine=False)
        self.ac1 = nn.Softplus()
        #self.rnn = nn.RNN(64,256,dropout=0.25)
        self.gru = nn.GRU(64,256,dropout=0.25)
        self.fc1 = nn.Linear(256, 64)
        self.fc2 = nn.Linear(64, num_classes)
        
    def forward(self, x):      
        x, _= self.gru(x)
        #print(x.shape)
        x = x[:,-1,:]
        #print(x.shape)
        x = self.fc1(x)
        x = self.bn1(x)
        x = self.ac1(x)
        x = self.d1(x)
        x = self.fc2(x)

        return x

In [6]:
rnn = BiGRU(4)
input = torch.randn(10, 64, 64)
output= rnn(input)
print(output.shape)

torch.Size([10, 4])


In [7]:
writer = SummaryWriter()

In [8]:
train_set = pd.read_csv("data/final_format/train_set.csv",header=None).to_numpy()
train_label = pd.read_csv("data/final_format/train_label.csv",header=None).to_numpy()
test_set = pd.read_csv("data/final_format/test_set.csv",header=None).to_numpy()
test_label = pd.read_csv("data/final_format/test_label.csv",header=None).to_numpy()

In [9]:
#delet first row data
train_set = train_set[1:]
train_label = train_label[1:]
test_set = test_set[1:]
test_label = test_label[1:]
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 4096) (14392, 1) (3598, 4096) (3598, 1)


In [10]:
train_label = train_label.reshape(-1)
test_label = test_label.reshape(-1)
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 4096) (14392,) (3598, 4096) (3598,)


In [11]:
#transpose to set data in time sequence
train_set = train_set.reshape(-1,64,64)
train_set = np.transpose(train_set,[0,2,1])
test_set = test_set.reshape(-1,64,64)
test_set = np.transpose(test_set,[0,2,1])
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 64, 64) (14392,) (3598, 64, 64) (3598,)


In [12]:
# Hyper parameters
num_epochs = 300
num_classes = 4
batch_size = 64
learning_rate = 1e-3

In [13]:
train_set_tensor = Tensor(train_set) 
train_label_tensor = Tensor(train_label).type(torch.LongTensor)

train_dataset = TensorDataset(train_set_tensor,train_label_tensor) 
train_loader = DataLoader(train_dataset, batch_size=batch_size) 

test_set_tensor = Tensor(test_set) 
test_label_tensor = Tensor(test_label).type(torch.LongTensor)

test_dataset = TensorDataset(test_set_tensor,test_label_tensor) 
test_loader = DataLoader(test_dataset, batch_size=batch_size) 

In [14]:
# Device configuration
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')
device

device(type='cuda', index=0)

In [15]:
model = BiGRU(num_classes).to(device)

In [16]:
# Loss and optimizer
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate, weight_decay=1e-3) 
#optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate) 
milestones = [50,100,150,200,250]
milestones = [a * len(train_loader) for a in milestones]
scheduler = MultiStepLR(optimizer, milestones=milestones, gamma=0.5)

In [17]:
# Train the model
total_step = len(train_loader)
for epoch in range(num_epochs):
    correct=0
    total=0
    running_loss = 0
    for i, (X, Y) in enumerate(train_loader):
        X = X.to(device)
        Y = Y.to(device)
        
        
        # Forward pass
        outputs = model(X)
        loss = criterion(outputs, Y)
        
        # Backward and optimize
        optimizer.zero_grad()
        loss.backward()
        #scheduler.step() 
        #print(scheduler.get_last_lr()[0])
      
        optimizer.step()
        scheduler.step() 
        #print(optimizer.param_groups[0]["lr"])
        
        _, predicted = outputs.max(1)
        total += Y.size(0)
        correct += predicted.eq(Y).sum().item()
        running_loss += loss.item()
        accu=100.*correct/total
        train_loss = running_loss/(i+1)
        print ('Epoch [{}/{}], Step [{}/{}], Training Accuracy: {:.4f}%, Training Loss: {:.4f}%'.format(epoch+1, num_epochs, i+1, total_step, accu, train_loss))
    
   
        #writer.add_scalar(f'train/accuracy', accu, epoch)
        #writer.add_scalar(f'train/loss', train_loss, epoch)
        writer.add_scalars(f'train/accuracy_loss', {
            'accuracy': accu,
            'loss': train_loss,
        }, epoch)
        

Epoch [1/300], Step [1/225], Training Accuracy: 20.3125%, Training Loss: 1.5314%
Epoch [1/300], Step [2/225], Training Accuracy: 23.4375%, Training Loss: 1.5104%
Epoch [1/300], Step [3/225], Training Accuracy: 22.9167%, Training Loss: 1.5129%
Epoch [1/300], Step [4/225], Training Accuracy: 25.3906%, Training Loss: 1.4929%
Epoch [1/300], Step [5/225], Training Accuracy: 24.0625%, Training Loss: 1.5003%
Epoch [1/300], Step [6/225], Training Accuracy: 23.1771%, Training Loss: 1.4946%
Epoch [1/300], Step [7/225], Training Accuracy: 22.9911%, Training Loss: 1.4929%
Epoch [1/300], Step [8/225], Training Accuracy: 25.0000%, Training Loss: 1.4821%
Epoch [1/300], Step [9/225], Training Accuracy: 24.3056%, Training Loss: 1.4807%
Epoch [1/300], Step [10/225], Training Accuracy: 23.9062%, Training Loss: 1.4759%
Epoch [1/300], Step [11/225], Training Accuracy: 23.5795%, Training Loss: 1.4716%
Epoch [1/300], Step [12/225], Training Accuracy: 24.2188%, Training Loss: 1.4677%
Epoch [1/300], Step [13/2

Epoch [1/300], Step [126/225], Training Accuracy: 27.6414%, Training Loss: 1.4108%
Epoch [1/300], Step [127/225], Training Accuracy: 27.6329%, Training Loss: 1.4107%
Epoch [1/300], Step [128/225], Training Accuracy: 27.7100%, Training Loss: 1.4103%
Epoch [1/300], Step [129/225], Training Accuracy: 27.6405%, Training Loss: 1.4106%
Epoch [1/300], Step [130/225], Training Accuracy: 27.6082%, Training Loss: 1.4106%
Epoch [1/300], Step [131/225], Training Accuracy: 27.6837%, Training Loss: 1.4104%
Epoch [1/300], Step [132/225], Training Accuracy: 27.6752%, Training Loss: 1.4099%
Epoch [1/300], Step [133/225], Training Accuracy: 27.6903%, Training Loss: 1.4101%
Epoch [1/300], Step [134/225], Training Accuracy: 27.6003%, Training Loss: 1.4105%
Epoch [1/300], Step [135/225], Training Accuracy: 27.6389%, Training Loss: 1.4101%
Epoch [1/300], Step [136/225], Training Accuracy: 27.6654%, Training Loss: 1.4100%
Epoch [1/300], Step [137/225], Training Accuracy: 27.6688%, Training Loss: 1.4092%
Epoc

Epoch [2/300], Step [19/225], Training Accuracy: 30.0164%, Training Loss: 1.3563%
Epoch [2/300], Step [20/225], Training Accuracy: 30.3125%, Training Loss: 1.3554%
Epoch [2/300], Step [21/225], Training Accuracy: 30.7292%, Training Loss: 1.3542%
Epoch [2/300], Step [22/225], Training Accuracy: 31.1080%, Training Loss: 1.3531%
Epoch [2/300], Step [23/225], Training Accuracy: 31.3859%, Training Loss: 1.3515%
Epoch [2/300], Step [24/225], Training Accuracy: 31.4453%, Training Loss: 1.3497%
Epoch [2/300], Step [25/225], Training Accuracy: 31.8750%, Training Loss: 1.3470%
Epoch [2/300], Step [26/225], Training Accuracy: 31.9111%, Training Loss: 1.3454%
Epoch [2/300], Step [27/225], Training Accuracy: 32.1181%, Training Loss: 1.3457%
Epoch [2/300], Step [28/225], Training Accuracy: 32.3103%, Training Loss: 1.3440%
Epoch [2/300], Step [29/225], Training Accuracy: 32.1659%, Training Loss: 1.3436%
Epoch [2/300], Step [30/225], Training Accuracy: 32.2917%, Training Loss: 1.3428%
Epoch [2/300], S

Epoch [2/300], Step [129/225], Training Accuracy: 32.1827%, Training Loss: 1.3415%
Epoch [2/300], Step [130/225], Training Accuracy: 32.1274%, Training Loss: 1.3417%
Epoch [2/300], Step [131/225], Training Accuracy: 32.1326%, Training Loss: 1.3418%
Epoch [2/300], Step [132/225], Training Accuracy: 32.0786%, Training Loss: 1.3419%
Epoch [2/300], Step [133/225], Training Accuracy: 32.1311%, Training Loss: 1.3420%
Epoch [2/300], Step [134/225], Training Accuracy: 32.1129%, Training Loss: 1.3425%
Epoch [2/300], Step [135/225], Training Accuracy: 32.1412%, Training Loss: 1.3423%
Epoch [2/300], Step [136/225], Training Accuracy: 32.1806%, Training Loss: 1.3421%
Epoch [2/300], Step [137/225], Training Accuracy: 32.1966%, Training Loss: 1.3419%
Epoch [2/300], Step [138/225], Training Accuracy: 32.1671%, Training Loss: 1.3418%
Epoch [2/300], Step [139/225], Training Accuracy: 32.1156%, Training Loss: 1.3421%
Epoch [2/300], Step [140/225], Training Accuracy: 32.1987%, Training Loss: 1.3416%
Epoc

Epoch [3/300], Step [17/225], Training Accuracy: 36.0294%, Training Loss: 1.3291%
Epoch [3/300], Step [18/225], Training Accuracy: 35.8507%, Training Loss: 1.3295%
Epoch [3/300], Step [19/225], Training Accuracy: 35.4441%, Training Loss: 1.3330%
Epoch [3/300], Step [20/225], Training Accuracy: 35.2344%, Training Loss: 1.3325%
Epoch [3/300], Step [21/225], Training Accuracy: 36.0863%, Training Loss: 1.3276%
Epoch [3/300], Step [22/225], Training Accuracy: 36.1506%, Training Loss: 1.3240%
Epoch [3/300], Step [23/225], Training Accuracy: 36.0054%, Training Loss: 1.3236%
Epoch [3/300], Step [24/225], Training Accuracy: 35.6120%, Training Loss: 1.3227%
Epoch [3/300], Step [25/225], Training Accuracy: 35.5625%, Training Loss: 1.3227%
Epoch [3/300], Step [26/225], Training Accuracy: 35.8774%, Training Loss: 1.3205%
Epoch [3/300], Step [27/225], Training Accuracy: 35.7639%, Training Loss: 1.3191%
Epoch [3/300], Step [28/225], Training Accuracy: 35.9375%, Training Loss: 1.3168%
Epoch [3/300], S

...

Epoch [298/300], Step [206/225], Training Accuracy: 99.7042%, Training Loss: 0.0169%
Epoch [298/300], Step [207/225], Training Accuracy: 99.7056%, Training Loss: 0.0169%
Epoch [298/300], Step [208/225], Training Accuracy: 99.7070%, Training Loss: 0.0169%
Epoch [298/300], Step [209/225], Training Accuracy: 99.7084%, Training Loss: 0.0168%
Epoch [298/300], Step [210/225], Training Accuracy: 99.7024%, Training Loss: 0.0169%
Epoch [298/300], Step [211/225], Training Accuracy: 99.7038%, Training Loss: 0.0170%
Epoch [298/300], Step [212/225], Training Accuracy: 99.7052%, Training Loss: 0.0169%
Epoch [298/300], Step [213/225], Training Accuracy: 99.7066%, Training Loss: 0.0169%
Epoch [298/300], Step [214/225], Training Accuracy: 99.7079%, Training Loss: 0.0169%
Epoch [298/300], Step [215/225], Training Accuracy: 99.7093%, Training Loss: 0.0168%
Epoch [298/300], Step [216/225], Training Accuracy: 99.7106%, Training Loss: 0.0168%
Epoch [298/300], Step [217/225], Training Accuracy: 99.7120%, Tra

Epoch [299/300], Step [82/225], Training Accuracy: 99.6951%, Training Loss: 0.0171%
Epoch [299/300], Step [83/225], Training Accuracy: 99.6988%, Training Loss: 0.0172%
Epoch [299/300], Step [84/225], Training Accuracy: 99.7024%, Training Loss: 0.0171%
Epoch [299/300], Step [85/225], Training Accuracy: 99.7059%, Training Loss: 0.0170%
Epoch [299/300], Step [86/225], Training Accuracy: 99.7093%, Training Loss: 0.0170%
Epoch [299/300], Step [87/225], Training Accuracy: 99.6947%, Training Loss: 0.0172%
Epoch [299/300], Step [88/225], Training Accuracy: 99.6982%, Training Loss: 0.0172%
Epoch [299/300], Step [89/225], Training Accuracy: 99.7015%, Training Loss: 0.0172%
Epoch [299/300], Step [90/225], Training Accuracy: 99.7049%, Training Loss: 0.0171%
Epoch [299/300], Step [91/225], Training Accuracy: 99.7081%, Training Loss: 0.0171%
Epoch [299/300], Step [92/225], Training Accuracy: 99.7113%, Training Loss: 0.0171%
Epoch [299/300], Step [93/225], Training Accuracy: 99.7144%, Training Loss: 

Epoch [299/300], Step [185/225], Training Accuracy: 99.6115%, Training Loss: 0.0181%
Epoch [299/300], Step [186/225], Training Accuracy: 99.6136%, Training Loss: 0.0181%
Epoch [299/300], Step [187/225], Training Accuracy: 99.6156%, Training Loss: 0.0180%
Epoch [299/300], Step [188/225], Training Accuracy: 99.6177%, Training Loss: 0.0180%
Epoch [299/300], Step [189/225], Training Accuracy: 99.6197%, Training Loss: 0.0179%
Epoch [299/300], Step [190/225], Training Accuracy: 99.6217%, Training Loss: 0.0180%
Epoch [299/300], Step [191/225], Training Accuracy: 99.6237%, Training Loss: 0.0179%
Epoch [299/300], Step [192/225], Training Accuracy: 99.6175%, Training Loss: 0.0180%
Epoch [299/300], Step [193/225], Training Accuracy: 99.6195%, Training Loss: 0.0179%
Epoch [299/300], Step [194/225], Training Accuracy: 99.6215%, Training Loss: 0.0179%
Epoch [299/300], Step [195/225], Training Accuracy: 99.6154%, Training Loss: 0.0179%
Epoch [299/300], Step [196/225], Training Accuracy: 99.6173%, Tra

Epoch [300/300], Step [64/225], Training Accuracy: 99.7559%, Training Loss: 0.0153%
Epoch [300/300], Step [65/225], Training Accuracy: 99.7596%, Training Loss: 0.0153%
Epoch [300/300], Step [66/225], Training Accuracy: 99.7633%, Training Loss: 0.0153%
Epoch [300/300], Step [67/225], Training Accuracy: 99.7668%, Training Loss: 0.0153%
Epoch [300/300], Step [68/225], Training Accuracy: 99.7702%, Training Loss: 0.0153%
Epoch [300/300], Step [69/225], Training Accuracy: 99.7736%, Training Loss: 0.0152%
Epoch [300/300], Step [70/225], Training Accuracy: 99.7768%, Training Loss: 0.0151%
Epoch [300/300], Step [71/225], Training Accuracy: 99.7579%, Training Loss: 0.0152%
Epoch [300/300], Step [72/225], Training Accuracy: 99.7613%, Training Loss: 0.0152%
Epoch [300/300], Step [73/225], Training Accuracy: 99.7646%, Training Loss: 0.0153%
Epoch [300/300], Step [74/225], Training Accuracy: 99.7466%, Training Loss: 0.0154%
Epoch [300/300], Step [75/225], Training Accuracy: 99.7500%, Training Loss: 

Epoch [300/300], Step [173/225], Training Accuracy: 99.7381%, Training Loss: 0.0155%
Epoch [300/300], Step [174/225], Training Accuracy: 99.7306%, Training Loss: 0.0156%
Epoch [300/300], Step [175/225], Training Accuracy: 99.7321%, Training Loss: 0.0156%
Epoch [300/300], Step [176/225], Training Accuracy: 99.7337%, Training Loss: 0.0157%
Epoch [300/300], Step [177/225], Training Accuracy: 99.7352%, Training Loss: 0.0157%
Epoch [300/300], Step [178/225], Training Accuracy: 99.7279%, Training Loss: 0.0158%
Epoch [300/300], Step [179/225], Training Accuracy: 99.7294%, Training Loss: 0.0158%
Epoch [300/300], Step [180/225], Training Accuracy: 99.7309%, Training Loss: 0.0157%
Epoch [300/300], Step [181/225], Training Accuracy: 99.7324%, Training Loss: 0.0157%
Epoch [300/300], Step [182/225], Training Accuracy: 99.7339%, Training Loss: 0.0157%
Epoch [300/300], Step [183/225], Training Accuracy: 99.7268%, Training Loss: 0.0158%
Epoch [300/300], Step [184/225], Training Accuracy: 99.7283%, Tra

In [18]:
from playsound import playsound
playsound(u"sound.mp3")

In [19]:
# Test the model
model.eval()  # eval mode (batchnorm uses moving mean/variance instead of mini-batch mean/variance)
with torch.no_grad():
    correct = 0
    total = 0
    for X, Y in test_loader:
        X = X.to(device)
        Y = Y.to(device)
        outputs = model(X)
        _, predicted = torch.max(outputs.data, 1)
        total += Y.size(0)
        correct += (predicted == Y).sum().item()

    print('Test Accuracy : {} %'.format(100 * correct / total))

# Save the model checkpoint
#torch.save(model.state_dict(), 'model.ckpt')

Test Accuracy : 35.8810450250139 %
